# Interactive maps

In this tutorial we will learn how to publish data from Python on interactive [leaflet.js](http://leafletjs.com/) maps. 

JavaScript (JS)  is a programming language for adding interactive content (such a zoomamble maps!) on webpages. [Leaflet](http://leafletjs.com/) is a popular JavaScript library for creating interactive maps for webpages ([OpenLayers](https://openlayers.org/) is another JavaScript library for the same purpose). 

Here, will mainly focus on [Folium](https://python-visualization.github.io/folium/) - a Python library that makes it easy to convert data from (Geo)DataFrames into interactive Leaflet maps.

<div class="alert alert-info">

**Explore also...**
    
Other interesting libraries for creating interactive visualizations from spatial data:
    
- [mapboxgl](https://github.com/mapbox/mapboxgl-jupyter)
- [Bokeh](https://docs.bokeh.org/en/latest/)
- [Geoviews](http://geoviews.org/)
- [plotly express](https://plotly.com/python/maps/)

</div>


## Folium


[Folium](https://github.com/python-visualization/folium)  is a Python library that makes
it possible visualize data on an interactive Leaflet map.

**Resources:**

- [Folium Documentation](https://python-visualization.github.io/folium/)
- [Example Gallery](https://nbviewer.jupyter.org/github/python-visualization/folium/tree/master/examples/)
- [Folium Quickstart](https://python-visualization.github.io/folium/quickstart.html)


### Creating a simple interactive web-map

Import folium and other useful packages:

In [1]:
import folium

In [2]:
from pyproj import crs
import geopandas as gpd
import matplotlib.pyplot as plt

We will start by creating a simple interactive web-map without any data on it. We just visualize OpenStreetMap on a specific location of the world.

First thing that we need to do is to create [a Map instance](https://python-visualization.github.io/folium/modules.html#folium.folium.Map) and define a location for zooming in the data: 

In [3]:
# Create a Map instance
m = folium.Map(location=[60.25,24.8], zoom_start=10)

The first parameter ``location`` takes a pair of lat, lon values as list as an input which will determine where the map will be positioned when user opens up the map. ``zoom_start`` -parameter adjusts the default zoom-level for the map (the higher the number the closer the zoom is). ``control_scale`` defines if map should have a scalebar or not.

Let's see what our map looks like: 

In [4]:
m

We can also save the map as a html file:

In [5]:
outfp = "base_map.html"
#m.save(outfp)


You should now see a html file in your working directory. You can open the file in a web-browser in order to see the map, or in a text editor in order to see the source definition.


Let's create another map with different settings (location, bacground map, zoom levels etc). See documentation of the [Map() object](https://python-visualization.github.io/folium/modules.html#folium.folium.Map) for all avaiable options.
    
``tiles`` -parameter is used for changing the background map provider and map style (see the [documentation](https://python-visualization.github.io/folium/modules.html#folium.folium.Map) for all in-built options).


In [6]:
# Let's change the basemap style to 'Stamen Toner'
m = folium.Map(location=[60.25,24.8], tiles='Stamen Toner' ,zoom_start=10)
m

### Adding layers to the map

Let's first have a look how we can add a simple [marker](https://python-visualization.github.io/folium/modules.html?highlight=marker#folium.map.Marker) on the webmap:

In [7]:
# Create a Map instance
m = folium.Map(location=[60.25,24.8], zoom_start=10)

# Add marker
# Run: help(folium.Icon) for more info about icons
folium.Marker(
    location=[60.20426,24.96179],
    popup='Kumpula Campus',
    icon=folium.Icon(color='green', icon='ok-sign')
).add_to(m)

#Show map
m

As mentioned, Folium combines the strenghts of data manipulation in Python with the mapping capabilities of Leaflet.js. Eventually, we would like to include the plotting of interactive maps as the last part of our data analysis workflow. 

Let's see how we can plot data from a geodataframe using folium.



In [8]:
# File path
points_fp = r"data/addresses.shp"

# Read the data
points = gpd.read_file(points_fp)

#Check input data
points.head()

address    id   
0              Kampinkuja 1, 00100 Helsinki, Finland  1001  \
1               Kaivokatu 8, 00101 Helsinki, Finland  1002   
2  Hermanstads strandsväg 1, 00580 Helsingfors, F...  1003   
3                  Itäväylä, 00900 Helsinki, Finland  1004   
4         Tyynenmerenkatu 9, 00220 Helsinki, Finland  1005   

                    geometry  
0  POINT (24.93017 60.16837)  
1  POINT (24.94189 60.16987)  
2  POINT (24.97740 60.18736)  
3  POINT (25.09196 60.21448)  
4  POINT (24.92148 60.15658)

- conver the points to GeoJSON features using folium:

In [9]:
# Convert points to GeoJSON
points_gjson = folium.features.GeoJson(points, name='Public Transport Stations')

In [10]:
# Check the GeoJSON features
#points_gjson.data.get('features')

Now we have our population data stored as GeoJSON format which basically contains the
data as text in a similar way that it would be written in the ``.geojson`` -file.

Add the points onto the Helsinki basemap:

In [11]:
# Create a Map instance
m = folium.Map(location=[60.25,24.8], zoom_start=10, tiles='cartodbpositron')

# Add points to the map instance
points_gjson.add_to(m)

# Alternative syntax for adding points to the map instance
#m.add_child(points_gjson)

#Show map
m

### Layer control

We can also add a `LayerControl` object on our map, which allows the user to control which map layers are visible. See the [documentation](http://python-visualization.github.io/folium/docs-v0.5.0/modules.html#folium.map.LayerControl) for available parameters (you can e.g. change the position of the layer control icon).

In [12]:
# Create a layer control object and add it to our map instance
folium.LayerControl().add_to(m)

#Show map
m

### Heatmap

[Folium plugins](https://python-visualization.github.io/folium/plugins.html) allow us to use popular tools available in leaflet. One of these plugins is [HeatMap](https://python-visualization.github.io/folium/plugins.html#folium.plugins.HeatMap), which creates a heatmap layer from input points. 

Let's visualize a heatmap of the public transport stations in Helsinki using the addresses input data. [folium.plugins.HeatMap](https://python-visualization.github.io/folium/plugins.html#folium.plugins.HeatMap) requires a list of points, or a numpy array as input, so we need to first manipulate the data a bit:

In [13]:
# Get x and y coordinates for each point
points['x'] = points['geometry'].x
points['y'] = points['geometry'].y
points.head()

# Create a list of coordinate pairs
'''folium uses y and x for heatmap'''
locations = list(zip(points['y'],points['x']))

Check the data:

In [14]:
locations

[(60.1683731, 24.9301701),
 (60.1698665, 24.9418933),
 (60.18735880000001, 24.9774004),
 (60.21448089999999, 25.0919641),
 (60.1565781, 24.9214846),
 (60.23489060000001, 25.0816923),
 (60.2033879, 25.042239),
 (60.2753891, 25.035855),
 (60.2633799, 25.0291078),
 (60.22243630000001, 24.8718598),
 (60.1711874, 24.94251),
 (60.2306474, 24.8840504),
 (60.240163, 24.877383),
 (60.22163339999999, 24.9483202),
 (60.25149829999999, 25.0125655),
 (60.2177823, 24.893153),
 (60.2485471, 24.86186),
 (60.2291135, 24.9670533),
 (60.1986856, 24.9334051),
 (60.22401389999999, 24.8609335),
 (60.2436961, 24.9934979),
 (60.24444239999999, 25.040583),
 (60.20966609999999, 25.0778094),
 (60.20751019999999, 25.1424936),
 (60.225599, 25.0756547),
 (60.2382054, 25.1080054),
 (60.18789030000001, 24.9609122),
 (60.19413939999999, 25.0291263),
 (60.18837519999999, 25.0068399),
 (60.1793862, 24.9494874),
 (60.1694809, 24.9337569),
 (60.16500139999999, 24.9250072),
 (60.159069, 24.9214046),
 (60.1719108, 24.946851

In [15]:
from folium.plugins import HeatMap

# Create a Map instance
m = folium.Map(location=[60.25,24.8], zoom_start=10, tiles='cartodbpositron')


# Add heatmap to map instance
# Available parameters: HeatMap(data, name=None, min_opacity=0.5, max_zoom=18, max_val=1.0, radius=25, blur=15, gradient=None, overlay=True, control=True, show=True)
HeatMap(locations).add_to(m)

# Show map
m

### Clustered point map

Let's visualize the address points (locations of transport stations in Helsinki) on top of the choropleth map using clustered markers using folium's [MarkerCluster](https://python-visualization.github.io/folium/plugins.html?highlight=marker%20cluster#folium.plugins.MarkerCluster) class.

In [16]:
from folium.plugins import MarkerCluster

In [17]:
# Create a Map instance
m = folium.Map(location=[60.25,24.8], zoom_start=10, tiles='cartodbpositron')

In [18]:
# Following this example: https://github.com/python-visualization/folium/blob/master/examples/MarkerCluster.ipynb

# Get x and y coordinates for each point
'''using locations from above'''

# Create a list of coordinate pairs


'using locations from above'

In [19]:
# Create a folium marker cluster
marker_cluster = MarkerCluster(locations)

# Add marker cluster to map
marker_cluster.add_to(m)

# Show map
m

### Choropleth map

Next, let's check how we can overlay a population map on top of a basemap using [folium's choropleth method](http://python-visualization.github.io/folium/docs-v0.5.0/modules.html#folium.folium.Map.choropleth). This method is able to read the geometries and attributes directly from a geodataframe. 
This example is modified from the [Folium quicksart](https://python-visualization.github.io/folium/quickstart.html#Choropleth-maps).

- First read in the population grid from HSY wfs like we did in [lesson 3](https://autogis-site.readthedocs.io/en/latest/notebooks/L3/03_spatial-join.html):

In [20]:
import geopandas as gpd
from pyproj import CRS
import requests
import geojson

# Specify the url for web feature service
url = 'https://kartta.hsy.fi/geoserver/wfs'

# Specify parameters (read data in json format).
# Available feature types in this particular data source: http://geo.stat.fi/geoserver/vaestoruutu/wfs?service=wfs&version=2.0.0&request=describeFeatureType
params = dict(service='WFS',
              version='2.0.0',
              request='GetFeature',
              typeName='asuminen_ja_maankaytto:Vaestotietoruudukko_2020',
              outputFormat='json')

# Fetch data from WFS using requests
r = requests.get(url, params=params)

# Create GeoDataFrame from geojson
data = gpd.GeoDataFrame.from_features(geojson.loads(r.content))
# Clean overall cell
data = data[data['index'] != 27699]
# Check the data
data.head()

geometry  index  asukkaita   
0  POLYGON ((25472499.995 6685998.998, 25472499.9...    703          5  \
1  POLYGON ((25472499.995 6684249.004, 25472499.9...    710          8   
2  POLYGON ((25472499.995 6683999.005, 25472499.9...    711          5   
3  POLYGON ((25472499.995 6682998.998, 25472499.9...    715         13   
4  POLYGON ((25472749.993 6690249.003, 25472749.9...    848          5   

   asvaljyys  ika0_9  ika10_19  ika20_29  ika30_39  ika40_49  ika50_59   
0         51      99        99        99        99        99        99  \
1         44      99        99        99        99        99        99   
2         90      99        99        99        99        99        99   
3         34      99        99        99        99        99        99   
4         53      99        99        99        99        99        99   

   ika60_69  ika70_79  ika_yli80  
0        99        99         99  
1        99        99         99  
2        99        99         99  
3        99        99         99  
4        99        99         99

In [21]:
from pyproj import CRS
# Define crs
data.crs = CRS.from_epsg(3879)

Re-project layer into WGS 84 (epsg: 4326)

In [22]:
# Re-project to WGS84
data = data.to_crs(epsg=4326)

# Check layer crs definition
print(data.crs)

EPSG:4326


Rename columns

In [23]:
# Change the name of a column
data = data.rename(columns={'asukkaita':'pop20'})

In [24]:
# Create a Geo-id which is needed by the Folium (it needs to have a unique identifier for each row)
'''folium needs an identifier which is a string object'''
data['geo-id'] = data.index.astype(str)


In [25]:
# Select only needed columns
data = data[['geo-id', 'pop20', 'geometry']]

# Convert to geojson (not needed for the simple coropleth map!)
#pop_json = data.to_json()

#check data
data.head()

geo-id  pop20                                           geometry
0      0      5  POLYGON ((24.50287 60.28562, 24.50284 60.28787...
1      1      8  POLYGON ((24.50311 60.26992, 24.50308 60.27216...
2      2      5  POLYGON ((24.50315 60.26767, 24.50311 60.26992...
3      3     13  POLYGON ((24.50328 60.25870, 24.50325 60.26094...
4      4      5  POLYGON ((24.50682 60.32378, 24.50678 60.32603...

Create an interactive choropleth map from the population grid:

In [26]:
# Create a Map instance
m = folium.Map(location=[60.25,24.8], tiles='cartodbpositron', zoom_start=11)

# Plot a choropleth map
# Notice: 'geoid' column that we created earlier needs to be assigned always as the first column
folium.Choropleth(
    geo_data=data,
    name='Population in 2020',
    columns=['geo-id','pop20'],
    data=data,
    fill_color='YlOrRd',
    key_on='feature.id',
    line_weight=0,
    legend_name='Population in Helsinki'
).add_to(m)

#Show map
m

### Tooltips

It is possible to add different kinds of pop-up messages and tooltips to the map. Here, it would be nice to see the population of each grid cell when you hover the mouse over the map. Unfortunately this functionality is not apparently implemented implemented in the Choropleth method we used before. 

Add tooltips, we can add tooltips to our map when plotting the polygons as GeoJson objects using the `GeoJsonTooltip` feature. (following examples from [here](http://nbviewer.jupyter.org/gist/jtbaker/57a37a14b90feeab7c67a687c398142c?flush_cache=true) and [here](https://nbviewer.jupyter.org/github/jtbaker/folium/blob/geojsonmarker/examples/GeoJsonMarkersandTooltips.ipynb))

For a quick workaround, we plot the polygons on top of the coropleth map as a transparent layer, and add the tooltip to these objects. *Note: this is not an optimal solution as now the polygon geometry get's stored twice in the output!*

In [27]:
# Convert points to GeoJson
folium.features.GeoJson(data,  
                        name='Labels',
                        style_function=lambda x: {'color':'transparent','fillColor':'transparent','weight':0},
                        tooltip=folium.features.GeoJsonTooltip(fields=['pop20'],
                                                                aliases = ['Population'],
                                                                labels=True,
                                                                sticky=False
                                                                            )
                       ).add_to(m)

m

Rember that you can also save the output as an html file: 

In [28]:
outfp = "choropleth_map.html"
#m.save(outfp)

Extra: check out plotly express for an alternative way of plotting an interactive Choropleth map [in here](https://plotly.com/python/mapbox-county-choropleth/).

In [29]:
import leafmap

In [30]:
map_lm = leafmap.Map(center=[60.25,24.8], zoom=10)

#add geodata frame points
#map_lm.add_gdf(points, 'Addresses')

#create cluster
'''map_lm.add_points_from_xy(
    points,
    x='x',
    y='y',
    name='Heat Map',
    add_legend=True
)'''

#create chloropleth
map_lm.add_data(
    data,
    column='pop20',
    scheme='Quantiles',
    cmap='YlOrRd',
    legend_title='Population',
    legend_position='bottomleft',
    k=7,
    info_mode='on_hover',
)

map_lm

Map(center=[60.25, 24.8], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_ou…

In [31]:
# Load an empty map
from keplergl import KeplerGl
map_1 = KeplerGl()
map_1

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


KeplerGl()